In [1]:
import pandas as pd
import nltk
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from nltk.stem import WordNetLemmatizer
import string
import contractions
from num2words import num2words
from textblob import TextBlob
from spellchecker import SpellChecker
import re
from decimal import Decimal
import plotly.express as px
nltk.download('punkt')
nltk.download('stopwords')
nltk.download('wordnet')
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

column_names = ['target','ids','date','flag','user','text']

df = pd.read_csv('/users/amulya/Downloads/sentiment_text_analysis.csv',encoding='ISO-8859-1', header=None, names=column_names)
df.head(2)
nulls = df.isnull().sum()
# print(nulls)
print(df['target'].value_counts())
print(df['flag'].value_counts())

# df['target'] = df['target'].replace({4:1})
df.head()

[nltk_data] Downloading package punkt to /Users/amulya/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to
[nltk_data]     /Users/amulya/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to /Users/amulya/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


target
0    800000
4    800000
Name: count, dtype: int64
flag
NO_QUERY    1600000
Name: count, dtype: int64


target         ids                          date      flag  \
0       0  1467810369  Mon Apr 06 22:19:45 PDT 2009  NO_QUERY   
1       0  1467810672  Mon Apr 06 22:19:49 PDT 2009  NO_QUERY   
2       0  1467810917  Mon Apr 06 22:19:53 PDT 2009  NO_QUERY   
3       0  1467811184  Mon Apr 06 22:19:57 PDT 2009  NO_QUERY   
4       0  1467811193  Mon Apr 06 22:19:57 PDT 2009  NO_QUERY   

              user                                               text  
0  _TheSpecialOne_  @switchfoot http://twitpic.com/2y1zl - Awww, t...  
1    scotthamilton  is upset that he can't update his Facebook by ...  
2         mattycus  @Kenichan I dived many times for the ball. Man...  
3          ElleCTF    my whole body feels itchy and like its on fire   
4           Karoli  @nationwideclass no, it's not behaving at all....

In [2]:
unwanted_columns = ['ids','date','flag','user']
df = df.drop(unwanted_columns,axis = 1)
size, dups = df.size, df.duplicated().sum()
df = df.drop_duplicates()

In [3]:
print(df['target'].value_counts())
df.info()

target
4    793506
0    790185
Name: count, dtype: int64
<class 'pandas.core.frame.DataFrame'>
Index: 1583691 entries, 0 to 1599999
Data columns (total 2 columns):
 #   Column  Non-Null Count    Dtype 
---  ------  --------------    ----- 
 0   target  1583691 non-null  int64 
 1   text    1583691 non-null  object
dtypes: int64(1), object(1)
memory usage: 36.2+ MB


In [4]:
df['target'] = df['target'].replace({4:1})

In [5]:
df.rename(columns = {'target': 'typeOfSentiment'}, inplace = True)

In [6]:
def textPreProcessing(df, column):
    df[column] = df[column].str.lower()
    df[column] = df[column].apply(lambda x:re.sub('[\d]','',x))
    df[column] = df[column].apply(lambda s: ' '.join(re.sub("(w+://S+)", " ", s).split()))
    df[column] = df[column].apply(word_tokenize)
    punctuation = set(string.punctuation)
    df[column] = df[column].apply(lambda tokens: [token for token in tokens if token not in punctuation])
    stop_words = set(stopwords.words('english'))
    df[column] = df[column].apply(lambda tokens: [token for token in tokens if token not in stop_words])
    lemmatizer = WordNetLemmatizer()
    df[column] = df[column].apply(lambda tokens: [lemmatizer.lemmatize(token) for token in tokens])
    df[column] = df[column].apply(lambda tokens: [contractions.fix(token) for token in tokens])
    df[column] = df[column].apply(lambda tokens: [token for token in tokens if token.isalnum()])
    df[column] = df[column].apply(lambda tokens: [token.strip() for token in tokens])
    df[column] = df[column].apply(lambda tokens: [num2words(token) if isinstance(token, int) else token if isinstance(token, Decimal) else token for token in tokens])
    df[column] = df[column].apply(lambda tokens: ' '.join(tokens))

    return df[column]

In [7]:
new_df = textPreProcessing(df,"text")

In [8]:
df.head()

typeOfSentiment                                               text
0                0  switchfoot http awww bummer shoulda got david ...
1                0  upset ca update facebook texting might cry res...
2                0  kenichan dived many time ball managed save res...
3                0                    whole body feel itchy like fire
4                0                nationwideclass behaving mad ca see

In [9]:
class_0 = df[df['typeOfSentiment'] == 0]
class_1 = df[df['typeOfSentiment'] == 1]
print(len(class_0))
print(len(class_1))
sampled_class_0 = class_0.sample(n=10000, random_state=42)
sampled_class_1 = class_1.sample(n=10000, random_state=42)
sample_df = pd.concat([sampled_class_0, sampled_class_1])
sample_df = sample_df.sample(frac=1, random_state=42).reset_index(drop=True)

790185
793506


In [10]:
print(sample_df.head(10))

   typeOfSentiment                                               text
0                1                      volleyball different position
1                0        jonasgrrl missryss really wish could though
2                0         http peanut butter cupcake yumyum want one
3                0                                              bored
4                1                                        want strive
5                1  finally caught sleep refreshed geared wrecking xd
6                1  let brought feel damn good pay shout out rappe...
7                0                 nssteph work till side world right
8                1  dancebekkadance hey thought might like esp gor...
9                0                                mercedesdg doubtful


In [11]:
sample_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 20000 entries, 0 to 19999
Data columns (total 2 columns):
 #   Column           Non-Null Count  Dtype 
---  ------           --------------  ----- 
 0   typeOfSentiment  20000 non-null  int64 
 1   text             20000 non-null  object
dtypes: int64(1), object(1)
memory usage: 312.6+ KB


In [12]:
from sklearn.feature_extraction.text import TfidfVectorizer
tfidfVectorizer = TfidfVectorizer()
tfidfMatrix = tfidfVectorizer.fit(sample_df['text'])
textMatrix = tfidfMatrix.transform(sample_df['text'])
textColumns = tfidfMatrix.get_feature_names_out()
textDummies = pd.DataFrame(textMatrix.toarray(), columns = textColumns)
sample_df.reset_index(drop=True, inplace=True)
textDummies.reset_index(drop=True, inplace=True)
sample_df = pd.concat([sample_df, textDummies], axis=1)

In [13]:
sample_df.head(5)

typeOfSentiment                                         text   aa  aaa  \
0                1                volleyball different position  0.0  0.0   
1                0  jonasgrrl missryss really wish could though  0.0  0.0   
2                0   http peanut butter cupcake yumyum want one  0.0  0.0   
3                0                                        bored  0.0  0.0   
4                1                                  want strive  0.0  0.0   

   aaaaa  aaaaaaaaa  aaaaaaaaaaaaaah  aaaaaaaaaahhhhhhhh  aaaaaaaaafter  \
0    0.0        0.0              0.0                 0.0            0.0   
1    0.0        0.0              0.0                 0.0            0.0   
2    0.0        0.0              0.0                 0.0            0.0   
3    0.0        0.0              0.0                 0.0            0.0   
4    0.0        0.0              0.0                 0.0            0.0   

   aaaaaaand  aaaaaahhhh  aaaaaand  aaaaaaw  aaaaache  aaaaand  aaaaawwwwwww  \
0        0.0         0.0       0.0      0.0       0.0      0.0           0.0   
1        0.0         0.0       0.0      0.0       0.0      0.0           0.0   
2        0.0         0.0       0.0      0.0       0.0      0.0           0.0   
3        0.0         0.0       0.0      0.0       0.0      0.0           0.0   
4        0.0         0.0       0.0      0.0       0.0      0.0           0.0   

   aaaah  aaaallll  aaaawwww  aaages  aaah  aaahg  aaahh  aaahhh  aaahhhh  \
0    0.0       0.0       0.0     0.0   0.0    0.0    0.0     0.0      0.0   
1    0.0       0.0       0.0     0.0   0.0    0.0    0.0     0.0      0.0   
2    0.0       0.0       0.0     0.0   0.0    0.0    0.0     0.0      0.0   
3    0.0       0.0       0.0     0.0   0.0    0.0    0.0     0.0      0.0   
4    0.0       0.0       0.0     0.0   0.0    0.0    0.0     0.0      0.0   

   aaaw  aafreen  aah  aahahahha  aahhh  aahhhh  aaliyon  aalmiray  aami  aan  \
0   0.0      0.0  0.0        0.0    0.0     0.0      0.0       0.0   0.0  0.0   
1   0.0      0.0  0.0        0.0    0.0     0.0      0.0       0.0   0.0  0.0   
2   0.0      0.0  0.0        0.0    0.0     0.0      0.0       0.0   0.0  0.0   
3   0.0      0.0  0.0        0.0    0.0     0.0      0.0       0.0   0.0  0.0   
4   0.0      0.0  0.0        0.0    0.0     0.0      0.0       0.0   0.0  0.0   

   aanjelicaa  aaron  aaronage  aaronrussell  aaronthehobt  aaronwhite  \
0         0.0    0.0       0.0           0.0           0.0         0.0   
1         0.0    0.0       0.0           0.0           0.0         0.0   
2         0.0    0.0       0.0           0.0           0.0         0.0   
3         0.0    0.0       0.0           0.0           0.0         0.0   
4         0.0    0.0       0.0           0.0           0.0         0.0   

   aarrgh  aarrrrggghhhhh  aaww  aawww  aaziz   ab  abalone  abandoned  abba  \
0     0.0             0.0   0.0    0.0    0.0  0.0      0.0        0.0   0.0   
1     0.0             0.0   0.0    0.0    0.0  0.0      0.0        0.0   0.0   
2     0.0             0.0   0.0    0.0    0.0  0.0      0.0        0.0   0.0   
3     0.0             0.0   0.0    0.0    0.0  0.0      0.0        0.0   0.0   
4     0.0             0.0   0.0    0.0    0.0  0.0      0.0        0.0   0.0   

   abbie  abbieharding  abbiirocks  abbot  abbott  abbybaby  abbycorfan  \
0    0.0           0.0         0.0    0.0     0.0       0.0         0.0   
1    0.0           0.0         0.0    0.0     0.0       0.0         0.0   
2    0.0           0.0         0.0    0.0     0.0       0.0         0.0   
3    0.0           0.0         0.0    0.0     0.0       0.0         0.0   
4    0.0           0.0         0.0    0.0     0.0       0.0         0.0   

   abbymathew  abc  abcdefgolden  abcdude  abd  abdesignsinc  abdomen  \
0         0.0  0.0           0.0      0.0  0.0           0.0      0.0   
1         0.0  0.0           0.0      0.0  0.0           0.0      0.0   
2         0.0  0.0           0.0      0.0  0.0           0.0  

In [14]:
sample_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 20000 entries, 0 to 19999
Columns: 25609 entries, typeOfSentiment to ð¾ð½ð¾
dtypes: float64(25607), int64(1), object(1)
memory usage: 3.8+ GB


In [15]:
sample_df = sample_df.loc[:,~sample_df.T.duplicated(keep='first')]

In [16]:
sample_df['typeOfSentiment']

0        1
1        0
2        0
3        0
4        1
5        1
6        1
7        0
8        1
9        0
10       0
11       0
12       1
13       1
14       1
15       0
16       1
17       1
18       0
19       0
20       0
21       0
22       1
23       1
24       0
25       1
26       1
27       1
28       1
29       0
30       0
31       1
32       1
33       1
34       1
35       1
36       1
37       0
38       1
39       1
40       1
41       1
42       0
43       0
44       1
45       1
46       1
47       0
48       1
49       0
50       1
51       1
52       1
53       1
54       0
55       1
56       0
57       1
58       1
59       1
60       0
61       1
62       1
63       1
64       0
65       1
66       0
67       0
68       1
69       1
70       0
71       0
72       0
73       1
74       1
75       1
76       1
77       0
78       0
79       0
80       1
81       0
82       1
83       1
84       1
85       1
86       0
87       0
88       0
89       1
90       0

In [17]:
sample_df = sample_df.drop('text',axis = 1)

In [18]:
from sklearn.preprocessing import MinMaxScaler
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import precision_score, recall_score, f1_score, confusion_matrix, roc_curve, roc_auc_score
from sklearn.model_selection import train_test_split
sample_df = sample_df.astype(str)
x = sample_df.drop('typeOfSentiment',axis =1)
y = sample_df['typeOfSentiment']

train, test, yTrain, yTest = train_test_split(x, y, test_size=0.2, random_state=42)

model = RandomForestClassifier()
model.fit(train, yTrain)

y_pred = model.predict(test)


In [19]:
from sklearn.metrics import accuracy_score
accuracy = accuracy_score(yTest, y_pred)
print(accuracy)
# precision = precision_score(yTest, y_pred)
# recall = recall_score(yTest, y_pred)
# f1 = f1_score(yTest, y_pred)
# conf_matrix = confusion_matrix(yTest, y_pred)
# print(f"Precision: {precision}")
# print(f"Recall: {recall}")
# print(f"F1 Score: {f1}")
# print(f"Confusion Matrix:\n{conf_matrix}")

0.72175


In [20]:
trainAccuracy = accuracy_score(yTrain, y_pred)
print(trainAccuracy)

ValueError: Found input variables with inconsistent numbers of samples: [16000, 4000]